In [4]:
import pandas as pd
import xlsxwriter
import requests
import os
from betting_functions import get_todays_game_ids, fetch_game_data

In [5]:
sportsbook = 'DraftKings (Pick 6)'
url = "https://api.opticodds.com/api/v3/markets"

        # Set the query parameters for baseball and DraftKings
params = {
            "key":'540d8b29-e704-403d-9926-363d3d7fcaff',
            "sport": "football",
            "sportsbook": 'DraftKings (Pick 6)',
            "league":'NFL'
        }

        # Send the request to the API
response = requests.get(url, params=params)

        # Check if the request was successful
if response.status_code == 200:
            # Print the JSON response from the API
    markets_data = response.json()
else:
    markets_data = {"error": f"Failed to retrieve data, status code: {response.status_code}"}



In [6]:
market_names_with_player = [market['name'] for market in markets_data['data'] if 'Player' in market['name']]
desired_markets = market_names_with_player


In [145]:
def fetch_game_data_pick_6(game_ids, api_key, market_type='player', league='MLB', sportsbooks=['DraftKings (Pick 6)','DraftKings'], include_player_name=True):
    """
    Fetch game data dynamically based on the market type (player or game).
    
    :param game_ids: List of game IDs to fetch odds for
    :param api_key: API key for OddsJam
    :param market_type: 'player' for player markets, 'game' for game markets
    :param sport: The sport to fetch markets for
    :param league: The league to fetch markets for
    :param sportsbooks: List of sportsbooks to fetch data from
    :param include_player_name: Whether to include player names (for player markets)
    :return: DataFrame with the fetched game data
    """
    if league == 'MLB':
        sport = 'baseball'
        markets = ['Player Hits + Runs + RBIs','Player Strikeouts','Player Hits','Player Hits Allowed','Player Singles']
    if league == 'NFL':
        sport = 'football'
        sportsbook = 'DraftKings (Pick 6)'
        url = "https://api.opticodds.com/api/v3/markets"

        # Set the query parameters for baseball and DraftKings
        params = {
        "key":'540d8b29-e704-403d-9926-363d3d7fcaff',
        "sport": "football",
        "sportsbook": 'DraftKings (pick)',
        "league":'NFL'
        }

    # Send the request to the API
        response = requests.get(url, params=params)

    # Check if the request was successful
        if response.status_code == 200:
        # Print the JSON response from the API
            markets_data = response.json()
        else:
            markets_data = {"error": f"Failed to retrieve data, status code: {response.status_code}"}
        market_names_with_player = [market['name'] for market in markets_data['data'] if 'Player' in market['name']]
        markets = market_names_with_player



    url = "https://api-external.oddsjam.com/api/v2/game-odds"
    all_data = []
    
    # Fetch data in chunks for each sportsbook and game ID
    for chunk in [game_ids[i:i + 5] for i in range(0, len(game_ids), 5)]:
        for sportsbook in sportsbooks:
            params = {
                'key': api_key,
                'sportsbook': sportsbook,
                'game_id': chunk,
                'market_name': markets
            }
            response = requests.get(url, params=params)
            if response.status_code == 200:
                data = response.json().get('data', [])
                all_data.extend(data)
            else:
                print(f"Error fetching data: {response.status_code} - {response.text}")
    
    # Convert the fetched data into a dataframe
    rows = []
    for game_data in all_data:
        print(game_data)
        home_team = game_data.get('home_team', 'Unknown')
        away_team = game_data.get('away_team', 'Unknown')
        odds_list = game_data.get('odds', [])
        
        for item in odds_list:
            row = {
                'Game ID': game_data.get('id', 'Unknown'),
                "Game Name": f"{home_team} vs {away_team}",
                "Bet Name": item.get('name', None),
                'Market Name': item.get('market_name', ''),
                'Sportsbook': item.get('sports_book_name', sportsbook),
                'line': item.get('bet_points', None),
                'Odds': item.get('price', None),
            }
            if include_player_name and market_type == 'player':
                row['Player Name'] = item.get('selection', 'Unknown')
            rows.append(row)
    
    return pd.DataFrame(rows)


def pick_6_data_mlb(league):
    if league == 'MLB':
        game_ids = get_todays_game_ids(league=league,api_key='540d8b29-e704-403d-9926-363d3d7fcaff')
    if league == 'NFL':
        game_ids = get_nfl_game_ids()
    df = fetch_game_data_pick_6(game_ids, api_key='540d8b29-e704-403d-9926-363d3d7fcaff', market_type='player', league=league, sportsbooks=['DraftKings (Pick 6)','DraftKings'], include_player_name=True)
    # Step 1: Filter the dataframe to keep only rows where the sportsbook is DraftKings
    df_draftkings = df[df['Sportsbook'] == 'DraftKings']

    # Step 2: Drop the "Pick 6" odds by filtering out DraftKings (Pick 6)
    df_pick6 = df[df['Sportsbook'] == 'DraftKings (Pick 6)']

    # Step 3: Merge the two dataframes based on relevant columns to align markets, without including Pick 6 odds
    merged_df = pd.merge(df_draftkings, df_pick6, 
                         on=['Game ID', 'Market Name', 'Bet Name', 'line', 'Player Name'], 
                         suffixes=('_DraftKings', '_Pick6'))
        # Function to determine 'More' or 'Less' based on the Bet Name
    def determine_more_or_less(row):
        if 'Over' in row['Bet Name']:
            return 'More'
        elif 'Under' in row['Bet Name']:
            return 'Less'
        return None

    # Applying the function to the dataframe
    merged_df['More_or_Less'] = merged_df.apply(determine_more_or_less, axis=1)

    # Format the output to match the style of the spreadsheet
    final_df = merged_df[['Player Name',"Game Name_DraftKings" ,'Market Name', 'line', 'More_or_Less', 'Odds_DraftKings']]
    final_df.columns = ['Player',"Game Name", 'Category', 'Number', 'More or Less', 'Odds']
    final_df_filtered = merged_df.loc[merged_df.groupby(['Player Name', 'Market Name'])['Odds_DraftKings'].idxmin()]

    # Step 2: Format the output to match the desired columns
    final_df_filtered_output = final_df_filtered[['Player Name','Game Name_DraftKings', 'Market Name', 'line', 'More_or_Less', 'Odds_DraftKings']]
    final_df_filtered_output.columns = ['Player', "Game",'Category', 'Number', 'More or Less', 'Odds']
    return final_df_filtered_output




In [147]:
final_df_filtered_output = fetch_game_data_pick_6(league='NFL')


TypeError: fetch_game_data_pick_6() missing 2 required positional arguments: 'game_ids' and 'api_key'

In [125]:

# Create separate DataFrames for each market category
market_categories = final_df_filtered_output['Category'].unique()

# Prepare a dictionary to store separate DataFrames for each market
market_tables = {market: final_df_filtered_output[final_df_filtered_output['Category'] == market] for market in market_categories}


output_excel_path = "baseball_pick6_markets.xlsx"

with pd.ExcelWriter(output_excel_path, engine='xlsxwriter') as writer:
    # Write the full list at the top with a title
    final_df_filtered_output.to_excel(writer, sheet_name='Markets Overview', index=False, startrow=1)
    worksheet = writer.sheets['Markets Overview']
    worksheet.write(0, 0, 'Full List')

    # Add each market-specific table below the full list, with a title and space between tables
    row_position = len(final_df_filtered_output) + 4  # Start a few rows after the full list with extra space
    for market, df in market_tables.items():
        worksheet.write(row_position - 1, 0, market)  # Add the market title above each table
        df.to_excel(writer, sheet_name='Markets Overview', index=False, startrow=row_position)
        row_position += len(df) + 4  # Add space and title for the next table


In [150]:
ids = get_todays_game_ids(api_key='540d8b29-e704-403d-9926-363d3d7fcaff',league='NFL')

/Users/colesprouse/Desktop/Projects/ev_betting/betting_functions.py:70: FutureWarning: In a future version of pandas, parsing datetimes with mixed time zones will raise an error unless `utc=True`. Please specify `utc=True` to opt in to the new behaviour and silence this warning. To create a `Series` with mixed offsets and `object` dtype, please use `apply` and `datetime.datetime.strptime`
  games_df['start_date'] = pd.to_datetime(games_df['start_date'])


In [151]:
df = fetch_game_data_pick_6(ids,api_key='540d8b29-e704-403d-9926-363d3d7fcaff',    market_type='player',

    league='NFL',
    sportsbooks=['DraftKings (Pick 6)','DraftKings'],
    include_player_name=True)


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [152]:
df

Game ID                                Game Name  \
0      18821-27927-25-00     Baltimore Ravens vs Cleveland Browns   
1      18821-27927-25-00     Baltimore Ravens vs Cleveland Browns   
2      18821-27927-25-00     Baltimore Ravens vs Cleveland Browns   
3      18821-27927-25-00     Baltimore Ravens vs Cleveland Browns   
4      18821-27927-25-00     Baltimore Ravens vs Cleveland Browns   
...                  ...                                      ...   
12197  32889-42288-24-40  Atlanta Falcons vs Tampa Bay Buccaneers   
12198  32889-42288-24-40  Atlanta Falcons vs Tampa Bay Buccaneers   
12199  32889-42288-24-40  Atlanta Falcons vs Tampa Bay Buccaneers   
12200  32889-42288-24-40  Atlanta Falcons vs Tampa Bay Buccaneers   
12201  32889-42288-24-40  Atlanta Falcons vs Tampa Bay Buccaneers   

                    Bet Name             Market Name  Sportsbook  line  \
0           Baltimore Ravens     First Team To Score  DraftKings   NaN   
1           Cleveland Browns     First Team To Score  DraftKings   NaN   
2           Baltimore Ravens               Moneyline  DraftKings   NaN   
3           Cleveland Browns               Moneyline  DraftKings   NaN   
4      Baltimore Ravens -4.5            Point Spread  DraftKings  -4.5   
...                      ...                     ...         ...   ...   
12197              Under 2.5         Total Turnovers  DraftKings   2.5   
12198                     No  Will There Be A Safety  DraftKings   NaN   
12199                    Yes  Will There Be A Safety  DraftKings   NaN   
12200                     No  Will There Be Overtime  DraftKings   NaN   
12201                    Yes  Will There Be Overtime  DraftKings   NaN   

         Odds       Player Name  
0      -140.0  Baltimore Ravens  
1       110.0  Cleveland Browns  
2      -205.0  Baltimore Ravens  
3       170.0  Cleveland Browns  
4      -110.0  Baltimore Ravens  
...       ...               ...  
12197  -105.0                    
12198 -2000.0                No  
12199  1000.0               Yes  
12200 -3500.0                No  
12201  1300.0               Yes  

[12202 rows x 8 columns]

In [ ]:
df

In [101]:
df = df[df['Market Name'].isin(desired_markets)]

In [102]:
# Step 1: Filter the dataframe to keep only rows where the sportsbook is DraftKings
df_draftkings = df[df['Sportsbook'] == 'DraftKings']

# Step 2: Drop the "Pick 6" odds by filtering out DraftKings (Pick 6)
df_pick6 = df[df['Sportsbook'] == 'DraftKings (Pick 6)']

# Step 3: Merge the two dataframes based on relevant columns to align markets, without including Pick 6 odds
merged_df = pd.merge(df_draftkings, df_pick6, 
                     on=['Game ID', 'Market Name', 'Bet Name', 'line', 'Player Name'], 
                     suffixes=('_DraftKings', '_Pick6'))


In [106]:
# Function to determine 'More' or 'Less' based on the Bet Name
def determine_more_or_less(row):
    if 'Over' in row['Bet Name']:
        return 'More'
    elif 'Under' in row['Bet Name']:
        return 'Less'
    return None

# Applying the function to the dataframe
merged_df['More_or_Less'] = merged_df.apply(determine_more_or_less, axis=1)

# Format the output to match the style of the spreadsheet
final_df = merged_df[['Player Name',"Game Name_DraftKings" ,'Market Name', 'line', 'More_or_Less', 'Odds_DraftKings']]
final_df.columns = ['Player',"Game Name", 'Category', 'Number', 'More or Less', 'Odds']


In [108]:
final_df_filtered = merged_df.loc[merged_df.groupby(['Player Name', 'Market Name'])['Odds_DraftKings'].idxmin()]

# Step 2: Format the output to match the desired columns
final_df_filtered_output = final_df_filtered[['Player Name','Game Name_DraftKings', 'Market Name', 'line', 'More_or_Less', 'Odds_DraftKings']]
final_df_filtered_output.columns = ['Player', "Game",'Category', 'Number', 'More or Less', 'Odds']


In [110]:
# Create separate DataFrames for each market category
market_categories = final_df_filtered_output['Category'].unique()

# Prepare a dictionary to store separate DataFrames for each market
market_tables = {market: final_df_filtered_output[final_df_filtered_output['Category'] == market] for market in market_categories}


In [111]:
output_excel_path = "baseball_pick6_markets.xlsx"

with pd.ExcelWriter(output_excel_path, engine='xlsxwriter') as writer:
    # Write the full list at the top with a title
    final_df_filtered_output.to_excel(writer, sheet_name='Markets Overview', index=False, startrow=1)
    worksheet = writer.sheets['Markets Overview']
    worksheet.write(0, 0, 'Full List')

    # Add each market-specific table below the full list, with a title and space between tables
    row_position = len(final_df_filtered_output) + 4  # Start a few rows after the full list with extra space
    for market, df in market_tables.items():
        worksheet.write(row_position - 1, 0, market)  # Add the market title above each table
        df.to_excel(writer, sheet_name='Markets Overview', index=False, startrow=row_position)
        row_position += len(df) + 4  # Add space and title for the next table


In [2]:
url = "https://api-external.oddsjam.com/api/v2/game-odds"
all_data = []
game_ids = ['13602-17463-24-41', '11434-82789-24-40', '16343-78014-24-40', '37430-25327-24-40', '39341-13184-24-40', '74813-26757-24-40', '16341-31124-24-40', '18124-24276-24-40', '18821-41522-24-40', '22677-37240-24-40', '27927-33320-24-40', '40716-28265-24-40', '37797-12806-24-40', '32889-42288-24-40']
sportsbooks = ['DraftKings','DraftKings (Pick 6)']
# Fetch data in chunks for each sportsbook and game ID
for chunk in [game_ids[i:i + 5] for i in range(0, len(game_ids), 5)]:
    for sportsbook in sportsbooks:
        params = {
            'key': '540d8b29-e704-403d-9926-363d3d7fcaff',
            'sportsbook': sportsbook,
            'game_id': chunk,
            'market_name': ['Player Passing Touchdowns', 'Player Interceptions', 'Player Receiving Yards', 'Player Passing Attempts', 'Player Passing Completions', 'Player Tackles + Assists', 'Player Receptions', 'Player Touchdowns', 'Player Kicking Points', 'Player Passing Yards', 'Player Rushing Yards', 'Player Rushing + Receiving Yards']
            }
        response = requests.get(url, params=params)
        if response.status_code == 200:
            data = response.json().get('data', [])
            all_data.extend(data)
        else:
            print(f"Error fetching data: {response.status_code} - {response.text}")


In [3]:
all_data

[{'id': '13602-17463-24-41',
  'start_date': '2024-10-08T00:15:00Z',
  'home_team': 'Kansas City Chiefs',
  'away_team': 'New Orleans Saints',
  'is_live': False,
  'is_popular': False,
  'tournament': None,
  'status': 'unplayed',
  'sport': 'football',
  'league': 'NFL',
  'odds': [{'id': '13602-17463-24-41:draftkings:player_passing_completions:derek_carr_over_20_5',
    'sports_book_name': 'DraftKings',
    'name': 'Derek Carr Over 20.5',
    'price': -115.0,
    'timestamp': 1727991559.0937512,
    'bet_points': 20.5,
    'is_main': True,
    'is_live': False,
    'market_name': 'Player Passing Completions',
    'market': 'player_passing_completions',
    'home_rotation_number': None,
    'away_rotation_number': None,
    'deep_link_url': 'https://sportsbook.draftkings.com/event/30568618?outcomes=0QA216118706%2357446862_13L88808Q1-1156597433Q20',
    'player_id': 'C12F49D17453',
    'selection': 'Derek Carr',
    'normalized_selection': 'derek_carr',
    'selection_line': 'over',
 